In [1]:
from ipynb.fs.full.Infer_propagation_path_functions import *


In [2]:
client = MongoClient('mongodb://localhost:27017/')

db = client.get_database('tweets')

In [3]:
COLLECTION_NAME = 'data_false_2'
tweets = db[COLLECTION_NAME].find({})
followers = db['followers'].find({})

tweet_user_ids = []
for tweet in tweets:
    tweet_user_ids.append(tweet['user']['id'])

tweet_user_ids

[57441414,
 22736172,
 557193955,
 3899337568,
 569513105,
 564158458,
 1254146990482395137,
 350165465,
 1301672012016947201,
 1190870943167594497,
 1374039117818904584,
 566479653,
 1222754262188482560,
 1622170904,
 178665364,
 4867635922,
 1229029861,
 1372967825120268298,
 841413934703902720,
 1258471016537325568,
 20422072,
 1303054664427081730,
 890832677548556288,
 1339710588008747009,
 1267538645486952453,
 4106923993,
 1563299498,
 888092403139198976,
 294824682,
 230691455,
 833013356,
 4458557717,
 443376427,
 3158134002,
 1490635454,
 961896485674725376,
 1291259699313115139,
 1154250308106641408,
 4017099076,
 9267212,
 218474991,
 20555838,
 739176138073907200,
 3078672341,
 586322289,
 1313774340215840769,
 146027825,
 1378351121631043587,
 1270453030824132608,
 1489476924,
 900325259764785153,
 48360202,
 15770253,
 2668527302,
 62935309,
 1925176123,
 418227801,
 877395414248378369,
 1130553464197488641,
 43827403,
 1380661593533341698,
 968708824600403969,
 891423165

In [14]:
'''
has a root user 1
root user has followers 1
If a root user followers intersects with tweets, they are cascade depth one users 1
if a cascade depth one user followers intersects with tweets, they are cascade depth two users
...
if a cascade depth n-1 user followers intersects with tweets, they are cascade depth n users

Lets say parent user publish a tweet and the child re-tweet that exact tweet.
child timestamp must be after the parent's time stamp
If child has many parents, parent with the most recent time stamp will be the owner of the child tweet  
'''
tweets = db[COLLECTION_NAME].find({})
#get root tweet
root_tweet = set()
for tweet in tweets:
    try:
        root_tweet.add(tweet['retweeted_status']['user']['id'])
    except KeyError as e:
        continue
print(root_tweet)

tweets = db[COLLECTION_NAME].find({})

# Create root node user_id, created_at

if len(root_tweet) == 1:
    for tweet in tweets:
        try:
            user_id = tweet['retweeted_status']['user']['id']
            created_at = tweet['retweeted_status']['created_at']
        except KeyError as e:
            continue
            
    print(user_id, created_at)

    root = Node(name = user_id, created_at = created_at, difference_seconds =  0)
    print(root.name)

    follower = db['followers'].find_one({'user_id' : root.name})
    try:
        print(follower['user_id'])
    except:
        print('None, DB does not have the user: ', root.name)
        
    #get depth 1 users

    if follower['user_id'] == root.name:
        root_followers = follower['followers']           

    root_followers

    tweets = db[COLLECTION_NAME].find({})
    followers = db['followers'].find({})

    tweet_user_ids = []
    for tweet in tweets:
        tweet_user_ids.append(tweet['user']['id'])

    tweet_user_ids

    cascade_depth_one_user_ids = list(set(root_followers) & set(tweet_user_ids))

    len(cascade_depth_one_user_ids)

    tweets = db[COLLECTION_NAME].find({})
    followers = db['followers'].find({})

    # add depth 1 users to the tree
    for user_id in cascade_depth_one_user_ids:
        tweets = db[COLLECTION_NAME].find({})
        for tweet in tweets:
            if tweet['user']['id'] == user_id:
                print(tweet['created_at'])
                difference = difference_datetime(tweet['created_at'], root.created_at).total_seconds()
                print(difference)
                globals()[f'user_{user_id}'] = Node(name = user_id, created_at = tweet['created_at'], difference_seconds = difference , parent = root)


    for pre, fill, node in RenderTree(root):
        print("%s user_id: %s, created_at: %s, difference_seconds: %s" % (pre, node.name, node.created_at, node.difference_seconds))
else:
    multiple_root_users(root_tweet)
#     raise('Cascade has more than one root user')

{57441414}
57441414 Wed May 12 06:53:36 +0000 2021
57441414
57441414
Wed May 12 22:23:35 +0000 2021
55799.0
Wed May 12 13:25:33 +0000 2021
23517.0
Wed May 12 07:47:04 +0000 2021
3208.0
Wed May 12 12:27:05 +0000 2021
20009.0
Wed May 12 10:08:41 +0000 2021
11705.0
Thu May 13 00:54:10 +0000 2021
64834.0
Wed May 12 18:16:03 +0000 2021
40947.0
Wed May 12 12:42:44 +0000 2021
20948.0
Wed May 12 10:19:43 +0000 2021
12367.0
Wed May 12 21:14:26 +0000 2021
51650.0
Thu May 13 01:37:54 +0000 2021
67458.0
Wed May 12 12:11:46 +0000 2021
19090.0
Wed May 12 07:25:24 +0000 2021
1908.0
Thu May 13 06:14:33 +0000 2021
84057.0
Wed May 12 16:19:34 +0000 2021
33958.0
Wed May 12 16:13:44 +0000 2021
33608.0
Wed May 12 10:58:08 +0000 2021
14672.0
Wed May 12 16:50:51 +0000 2021
35835.0
Wed May 12 12:43:30 +0000 2021
20994.0
Wed May 12 06:58:48 +0000 2021
312.0
Wed May 12 16:37:25 +0000 2021
35029.0
Wed May 12 07:00:07 +0000 2021
391.0
Thu May 13 05:40:53 +0000 2021
82037.0
Thu May 13 03:44:36 +0000 2021
75060.0
W

In [14]:
# export tree
from anytree.exporter import JsonExporter, DictExporter
exporter = DictExporter()
data = exporter.export(root)
with open(COLLECTION_NAME + '_tree.json', 'w') as fp:
    json.dump(data, fp)    

In [4]:
# import tree
from anytree.importer import DictImporter
from anytree import RenderTree
importer = DictImporter()
with open('data_false_2_tree.json', 'r') as fp:
    data = fp.readline()
data = json.loads(data)
root = importer.import_(data)
print(RenderTree(root))

AnyNode(created_at='Wed May 12 06:53:36 +0000 2021', difference_seconds=0, name=57441414)
├── AnyNode(created_at='Wed May 12 22:23:35 +0000 2021', difference_seconds=55799.0, name=2303475712)
├── AnyNode(created_at='Wed May 12 13:25:33 +0000 2021', difference_seconds=23517.0, name=395476995)
├── AnyNode(created_at='Wed May 12 07:47:04 +0000 2021', difference_seconds=3208.0, name=1157451503562559488)
├── AnyNode(created_at='Wed May 12 12:27:05 +0000 2021', difference_seconds=20009.0, name=1373852964809494539)
├── AnyNode(created_at='Wed May 12 10:08:41 +0000 2021', difference_seconds=11705.0, name=1298769595034218498)
├── AnyNode(created_at='Thu May 13 00:54:10 +0000 2021', difference_seconds=64834.0, name=2402394152)
├── AnyNode(created_at='Wed May 12 18:16:03 +0000 2021', difference_seconds=40947.0, name=841056307)
├── AnyNode(created_at='Wed May 12 12:42:44 +0000 2021', difference_seconds=20948.0, name=538542132)
├── AnyNode(created_at='Wed May 12 10:19:43 +0000 2021', difference_sec

In [5]:
add_depth_nodes(root, 2, tweet_user_ids, db, COLLECTION_NAME)

[AnyNode(created_at='Wed May 12 22:23:35 +0000 2021', difference_seconds=55799.0, name=2303475712), AnyNode(created_at='Wed May 12 13:25:33 +0000 2021', difference_seconds=23517.0, name=395476995), AnyNode(created_at='Wed May 12 07:47:04 +0000 2021', difference_seconds=3208.0, name=1157451503562559488), AnyNode(created_at='Wed May 12 12:27:05 +0000 2021', difference_seconds=20009.0, name=1373852964809494539), AnyNode(created_at='Wed May 12 10:08:41 +0000 2021', difference_seconds=11705.0, name=1298769595034218498)]
 user_id: 57441414, diff_s: 0
├──  user_id: 2303475712, diff_s: 55799.0
├──  user_id: 395476995, diff_s: 23517.0
│   ├──  user_id: 1258259392463601666, diff_s: 27004.0
│   ├──  user_id: 1324490405145051136, diff_s: 8915.0
│   ├──  user_id: 1388360760544407552, diff_s: 8022.0
│   ├──  user_id: 389475975, diff_s: 18989.0
│   ├──  user_id: 164659464, diff_s: 9671.0
│   ├──  user_id: 915991337933078531, diff_s: 11739.0
│   ├──  user_id: 2283962508, diff_s: 10900.0
│   ├──  user_

AnyNode(created_at='Wed May 12 06:53:36 +0000 2021', difference_seconds=0, name=57441414)

In [9]:
remove_duplicates(root)

602
1127


In [8]:
add_depth_nodes(root, 3, tweet_user_ids, db, COLLECTION_NAME)

[Node('/57441414/3296870476/844608168831397889', created_at='Thu May 13 06:15:01 +0000 2021', difference_seconds=28.0), Node('/57441414/3296870476/1262431623242551296', created_at='Thu May 13 22:54:18 +0000 2021', difference_seconds=59985.0), Node('/57441414/726161631160455168/1104841482085773313', created_at='Wed May 12 17:02:49 +0000 2021', difference_seconds=2595.0), Node('/57441414/526794855/864398492306989057', created_at='Wed May 12 08:19:46 +0000 2021', difference_seconds=4779.0), Node('/57441414/526794855/1143953805563912193', created_at='Wed May 12 07:06:56 +0000 2021', difference_seconds=409.0)]
 user_id: 57441414, diff_s: 0
├──  user_id: 1373852964809494539, diff_s: 20009.0
├──  user_id: 538542132, diff_s: 20948.0
├──  user_id: 3059007541, diff_s: 51650.0
├──  user_id: 2298634316, diff_s: 1908.0
├──  user_id: 3296870476, diff_s: 84057.0
│   ├──  user_id: 844608168831397889, diff_s: 28.0
│   └──  user_id: 1262431623242551296, diff_s: 59985.0
├──  user_id: 726161631160455168, 

AnyNode(created_at='Wed May 12 06:53:36 +0000 2021', difference_seconds=0, name=57441414)

In [13]:
for i in range(4,10):
    add_depth_nodes(root, i, tweet_user_ids, db, COLLECTION_NAME)
    remove_duplicates(root)

[Node('/57441414/726161631160455168/1104841482085773313/1247723843424112641', created_at='Fri May 14 14:34:39 +0000 2021', difference_seconds=163910.0), Node('/57441414/526794855/864398492306989057/1286380573817212931', created_at='Wed May 12 12:38:46 +0000 2021', difference_seconds=15540.0), Node('/57441414/526794855/1143953805563912193/2250696710', created_at='Wed May 12 10:27:15 +0000 2021', difference_seconds=12019.0), Node('/57441414/526794855/1143953805563912193/19247128', created_at='Wed May 12 11:10:23 +0000 2021', difference_seconds=14607.0), Node('/57441414/526794855/1143953805563912193/18190361', created_at='Wed May 12 07:16:16 +0000 2021', difference_seconds=560.0)]
 user_id: 57441414, diff_s: 0
├──  user_id: 1373852964809494539, diff_s: 20009.0
├──  user_id: 538542132, diff_s: 20948.0
├──  user_id: 3059007541, diff_s: 51650.0
├──  user_id: 2298634316, diff_s: 1908.0
├──  user_id: 3296870476, diff_s: 84057.0
│   ├──  user_id: 844608168831397889, diff_s: 28.0
│   └──  user_i

In [15]:
db[COLLECTION_NAME].find_one({'retweeted_status.user.id' : 57441414})['text']

"RT @ZubyMusic: The Merriam-Webster dictionary has changed their definition of 'anti-vaxxer' to include\n\n'people who oppose laws that mandat…"